# Modeling: Body color assignment and usage

In PyAnsys Geometry, a *body* represents solids or surfaces organized within the ``Design`` assembly.
As users might be already familiar with, Ansys CAD products (like SpaceClaim, Ansys Discovery and the
Geometry Service), allow to assign colors to bodies. This example shows how to assign colors to a body,
retrieve their value and how to use them in the client-side visualization.

## Perform required imports

Perform the required imports.

In [1]:
import ansys.geometry.core as pyansys_geometry

from ansys.geometry.core import launch_modeler
from ansys.geometry.core.math import Point2D, UNITVECTOR3D_X, UNITVECTOR3D_Y
from ansys.geometry.core.sketch import Sketch

## Create a box sketch

Create a ``Sketch`` instance and insert a box sketch with a width and height of 10
in the default plane.

In [2]:
sketch = Sketch()
sketch.box(Point2D([0, 0]), 10, 10)

## Initiate design on server

Establish a server connection and initiate a design on the server.

In [3]:
modeler = launch_modeler()
design = modeler.create_design("ServiceColors")

WARNING -  -  docker_instance - _check_port_availability - Service is already running at port 700...


/home/runner/work/pyansys-geometry/pyansys-geometry/.venv/lib/python3.13/site-packages/ansys/tools/common/cyberchannel.py:188: UserWarning: Starting gRPC client without TLS on localhost:700. This is INSECURE. Consider using a secure connection.
  warn(f"Starting gRPC client without TLS on {target}. This is INSECURE. Consider using a secure connection.")


## Extrude the box sketch to create the matrix style design

Given the initial sketch, you can extrude it to create a matrix style design.
In this example, you can create a 2x3 matrix of bodies. Each body is separated by 30 units
in the X direction and 30 units in the Y direction. You have a total of 6 bodies.

In [4]:
translate = [[0, 30, 60], [0, 30, 60]]

for r_idx, row in enumerate(translate):
    comp = design.add_component(f"Component{r_idx}")

    for b_idx, dist in enumerate(row):
        body = comp.extrude_sketch(f"Component{r_idx}_Body{b_idx}", sketch, distance=10)
        body.translate(UNITVECTOR3D_Y, r_idx*30)
        body.translate(UNITVECTOR3D_X, dist)

design.plot()

EmbeddableWidget(value='<iframe srcdoc="<!DOCTYPE html>\n<html>\n  <head>\n    <meta http-equiv=&quot;Content-…

## Assign colors to the bodies

Given the previous design, you can assign a color to each body. You could have done
this assignment while creating the bodies, but for the sake of encapsulating the
color assignment logic, it is done in its own code cell.

In [5]:
colors = [["red", "blue", "yellow"], ["orange", "green", "purple"]]

for c_idx, comp in enumerate(design.components):
    for b_idx, body in enumerate(comp.bodies):
        body.color = colors[c_idx][b_idx]
        print(f"Body {body.name} has color {body.color}")

Body Component0_Body0 has color #ff0000ff
Body Component0_Body1 has color #0000ffff
Body Component0_Body2 has color #ffff00ff
Body Component1_Body0 has color #ffa500ff
Body Component1_Body1 has color #008000ff
Body Component1_Body2 has color #800080ff


## Plotting the design with colors

By default, the plot method does **not** use the colors assigned to the bodies.
To plot the design with the assigned colors, you need to specifically request it.

Users have two options for plotting with the assigned colors:

* Pass the parameter ``use_service_colors=True`` to the plot method.
* Set the global parameter ``USE_SERVICE_COLORS`` to ``True``.

It is important to note that the usage of colors when plotting might slow down the
plotting process, as it requires additional information to be sent from the server
to the client and processed in the client side.

If you just request the plot without setting the global parameter, the plot will
be displayed without the colors, as shown below.

In [6]:
design.plot()

EmbeddableWidget(value='<iframe srcdoc="<!DOCTYPE html>\n<html>\n  <head>\n    <meta http-equiv=&quot;Content-…

As stated previously, if you pass the parameter ``use_service_colors=True`` to the plot
method, the plot is displayed with the assigned colors.

In [7]:
design.plot(use_service_colors=True)

EmbeddableWidget(value='<iframe srcdoc="<!DOCTYPE html>\n<html>\n  <head>\n    <meta http-equiv=&quot;Content-…

However, if you set the global parameter to ``True``, the plot is displayed
with the assigned colors without the need to pass the parameter to the plot method.

In [8]:
import ansys.geometry.core as pyansys_geometry

pyansys_geometry.USE_SERVICE_COLORS = True

design.plot()

# Reverting the global parameter to its default value
pyansys_geometry.USE_SERVICE_COLORS = False

EmbeddableWidget(value='<iframe srcdoc="<!DOCTYPE html>\n<html>\n  <head>\n    <meta http-equiv=&quot;Content-…

This last method is useful when the user wants to plot all the designs with the
assigned colors without the need to pass the parameter to the plot method in
every call.


## Plotting specific bodies or components with colors

If the user wants to plot specific bodies with the assigned colors, the user can
follow the same approach as before. The user can pass the parameter ``use_service_colors=True``
to the plot method or set the global parameter ``USE_SERVICE_COLORS`` to ``True``.

In the following examples, you are shown how to do this using the
``use_service_colors=True`` parameter.

Let's plot the first body of the first component with the assigned colors.

In [9]:
body = design.components[0].bodies[0]

body.plot(use_service_colors=True)

EmbeddableWidget(value='<iframe srcdoc="<!DOCTYPE html>\n<html>\n  <head>\n    <meta http-equiv=&quot;Content-…

Now, let's plot the second component with the assigned colors.

In [10]:
comp = design.components[1]

comp.plot(use_service_colors=True)

EmbeddableWidget(value='<iframe srcdoc="<!DOCTYPE html>\n<html>\n  <head>\n    <meta http-equiv=&quot;Content-…